# Your first scraper
In this project, we will guide you step by step through the process of:

1. creating a self-contained development environment.
1. retrieving some information from an API (a website for computers)
2. leveraging it to scrape a website that does not provide an API
3. saving the output for later processing

Here we query an API for a list of countries and their past leaders. We then extract and sanitize their short bio from Wikipedia. Finally, we save the data to disk.

This task is often the first (coding) step of a datascience project and you will often come back to it in the future.

You will study topics such as *scraping*, *data structures*, *regular expressions*, *concurrency* and *file handling*. We will point out useful resources at the appropriate time. 

Let's dive in!

## Creating a clean environment

Use the [`venv`](https://docs.python.org/3/library/venv.html) command to create a new environment called `wikipedia_scraper`.

You will find more info about virtual environments [here](../../2.python/1.python_fundamentals/02.Package-Managers/00.Package_Managers.md).

Activate it and find a way to use it for this notebook.

## API Scraping

### A simple API query
You will start with the basics: how to do a simple request to an [API endpoint](../../2.python/2.python_advanced/05.Scraping/5.apis.ipynb).

You will use the [requests](https://requests.readthedocs.io/en/latest/) external library through the `import` keyword.

NOTE: external libraries need to be installed first. Check their documentation.

Check the [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/) section of the Requests documentation to:
1. use the `get()` method to connect to this endpoint: `https://country-leaders.herokuapp.com/status`
2. check if the `status_code` is equal to 200, which means OK.
    * if OK, `print()` the `text`` of the response.
    * if not, `print()` the `status_code`. 

Here is the signification of [HTTP status codes](https://en.wikipedia.org/wiki/List_of_HTTP_status_codes).


In [1]:
# import the requests library (1 line)
import requests

# assign the root url (without /status) to the root_url variable for ease of reference (1 line)
root_url = "https://country-leaders.herokuapp.com"

# assign the /status endpoint to another variable called status_url (1 line)
status_url = "/status"

# query the /status endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(f"{root_url}{status_url}")
# check the status_code using a condition and print appropriate messages (4 lines)

if req.status_code == 200:
    print(req.text)
else:
    print(req.status_code)




"Alive"


### Dealing with JSON

[JSON](https://quickref.me/json) is the preferred format to deal with data over the web. You cannot avoid it so you would better get acquainted.

Connect to another endpoint called `/countries` but this time the API will return data in the JSON format. Check what to do in the Requests [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/).


In [2]:
# Set the country_url variable (1 line)
country_url = "/countries"

# query the /country endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(f"{root_url}{country_url}")

# Get the JSON content and store it in the countries variable (1 line)
countries = req.json()

# display the request's status code and the countries variable (1 line)
display(req.status_code, countries)


403

{'message': 'The cookie is missing'}

### Cookies anyone?

It looks like the access to this API is restricted...
Query the `/cookie` endpoint and extract the appropriate field to access your cookie.

You will need to use this cookie in each of the following API requests.

In [3]:
# Set the cookie_url variable (1 line)
cookie_url = "/cookie"

# Query the enpoint, set the cookies variable and display it (3 lines)
req = requests.get(f"{root_url}{cookie_url}")
cookies =req.json()
print(cookies)


{'message': 'The cookie has been created'}


Try to query the countries endpoint using the cookie, save the output and print it.

In [4]:
# query the /countries endpoint, assign the output to the countries variable (1 line)
countries = requests.get(f"{root_url}{country_url}",cookies = req.cookies)
# and check the status code and the countries variable's content (3 lines)
print(countries.status_code)
print(countries.json())

200
['ru', 'fr', 'be', 'us', 'ma']


Chances are the cookie has expired... Thanksfully, you got a nice error message. For now, simply execute the last 2 cells quickly so you get a result.

### Getting the actual data from the API

Query the `/leaders` endpoint.

In [5]:
# Set the leaders_url variable (1 line)
leaders_url = "/leaders"
# query the /leaders endpoint, assign the output to the leaders variable (1 line)
leaders = requests.get(f"{root_url}{leaders_url}", cookies = req.cookies)
# and check its content (4 lines)
if leaders.status_code == 200:
    print(leaders.status_code, leaders.json())
else:
    print(leaders.status_code, " :not accessible")


404  :not accessible


It looks like this endpoint requires additional information in order to return its result. Check the API [*documentation*](https://country-leaders.herokuapp.com/docs) in your web browser.

Change the query to accept *parameters*. You should know where to find help by now.

In [6]:


# query the /leaders endpoint using cookies and parameters (take any country in countries)
params = {
    "country": "be"
}
leaders = requests.get(f"{root_url}{leaders_url}", cookies = req.cookies, params =params)
# check the result (3 lines) 
if leaders.status_code == 200:
    print(leaders.json())
else: print(leaders.status_code, " : Not accessible")
    



[{'id': 'Q12978', 'first_name': 'Guy', 'last_name': 'Verhofstadt', 'birth_date': '1953-04-11', 'death_date': None, 'place_of_birth': 'Dendermonde', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt', 'start_mandate': '1999-07-12', 'end_mandate': '2008-03-20'}, {'id': 'Q12981', 'first_name': 'Yves', 'last_name': 'Leterme', 'birth_date': '1960-10-06', 'death_date': None, 'place_of_birth': 'Wervik', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme', 'start_mandate': '2009-11-25', 'end_mandate': '2011-12-06'}, {'id': 'Q12983', 'first_name': 'Herman', 'last_name': 'Van Rompaey', 'birth_date': '1947-10-31', 'death_date': None, 'place_of_birth': 'Etterbeek', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Herman_Van_Rompuy', 'start_mandate': '2008-12-30', 'end_mandate': '2009-11-25'}, {'id': 'Q14989', 'first_name': 'Léon', 'last_name': 'Delacroix', 'birth_date': '1867-12-27', 'death_date': '1929-10-15', 'place_of_birth': 'Saint-Josse-ten-Noode', 'wikipedia_url': 'htt

### A sneak peak at the data (finally)

Look inside a few examples. Notice the dictionary keys available for each entry. You have your first example of *structured data*. This data was sanitized for your benefit, meaning it is readily exploitable without modification.

You will also notice there is a Wikipedia link for each entry. You will need to extract additional information there. This will be a case of *semi-structured* data.

The /countries endpoint returns a `list` of several country codes.

You need to loop through this list and query the /leaders endpoint for each one. Save each entry in a dictionary called `leaders_per_country` like this one: 
`{'fr':[{leader0}, {leader1},...],
'en':[{leader0}, {leader1},...],
...
}`.

In [7]:
# 5 lines
leaders_per_country = {}
#print(countries,type(countries))
for country in countries.json():
    leaders  = requests.get(f"{root_url}{leaders_url}", cookies = req.cookies, params ={"country":country}) 
    leaders_per_country[country] = leaders.json()
print(leaders_per_country)
    

{'ru': [{'id': 'Q7747', 'first_name': 'Vladimir', 'last_name': 'Putin', 'birth_date': '1952-10-07', 'death_date': None, 'place_of_birth': 'Saint Petersburg', 'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9F%D1%83%D1%82%D0%B8%D0%BD,_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80%D0%BE%D0%B2%D0%B8%D1%87', 'start_mandate': '2000-05-07', 'end_mandate': '2008-05-07'}, {'id': 'Q23530', 'first_name': 'Dmitry', 'last_name': 'Medvedev', 'birth_date': '1965-09-14', 'death_date': None, 'place_of_birth': 'Saint Petersburg', 'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9C%D0%B5%D0%B4%D0%B2%D0%B5%D0%B4%D0%B5%D0%B2,_%D0%94%D0%BC%D0%B8%D1%82%D1%80%D0%B8%D0%B9_%D0%90%D0%BD%D0%B0%D1%82%D0%BE%D0%BB%D1%8C%D0%B5%D0%B2%D0%B8%D1%87', 'start_mandate': '2008-05-07', 'end_mandate': '2012-05-07'}, {'id': 'Q34453', 'first_name': 'Boris', 'last_name': 'Yeltsin', 'birth_date': '1931-02-01', 'death_date': '2007-04-23', 'place_of_birth': 'Butka', 'wikipe

It is finally time to create a `get_leaders()` function for the above code. You will build on it later-on. This function takes no parameter. Inside it, you will need to:
1. define the urls
2. get the cookies
2. get the countries
3. loop over them and save their leaders in a dictionary
4. return the dictionary

In [8]:
# 15 lines
def get_leaders():
    root_url = "https://country-leaders.herokuapp.com"
    country_url = "/countries"
    cookie_url = "/cookie"
    leaders_url = "/leaders"
    req = requests.get(f"{root_url}{cookie_url}")
    cookies =req.json()
    countries = requests.get(f"{root_url}{country_url}",cookies = req.cookies)
    dic = {}
    #print(countries,type(countries))
    for country in countries.json():
        leaders  = requests.get(f"{root_url}{leaders_url}", cookies = req.cookies, params ={"country":country}) 
        dic[country] = leaders.json()
    return dic


    
    
get_leaders()

{'ru': [{'id': 'Q7747',
   'first_name': 'Vladimir',
   'last_name': 'Putin',
   'birth_date': '1952-10-07',
   'death_date': None,
   'place_of_birth': 'Saint Petersburg',
   'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9F%D1%83%D1%82%D0%B8%D0%BD,_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80%D0%BE%D0%B2%D0%B8%D1%87',
   'start_mandate': '2000-05-07',
   'end_mandate': '2008-05-07'},
  {'id': 'Q23530',
   'first_name': 'Dmitry',
   'last_name': 'Medvedev',
   'birth_date': '1965-09-14',
   'death_date': None,
   'place_of_birth': 'Saint Petersburg',
   'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9C%D0%B5%D0%B4%D0%B2%D0%B5%D0%B4%D0%B5%D0%B2,_%D0%94%D0%BC%D0%B8%D1%82%D1%80%D0%B8%D0%B9_%D0%90%D0%BD%D0%B0%D1%82%D0%BE%D0%BB%D1%8C%D0%B5%D0%B2%D0%B8%D1%87',
   'start_mandate': '2008-05-07',
   'end_mandate': '2012-05-07'},
  {'id': 'Q34453',
   'first_name': 'Boris',
   'last_name': 'Yeltsin',
   'birth_date': '1931-02-01',
 

Test your function, save the result in the `leaders_per_country` dictionary and check its ouput.

In [9]:
# 2 lines
leaders_per_country = get_leaders()
print(leaders_per_country)


{'ru': [{'id': 'Q7747', 'first_name': 'Vladimir', 'last_name': 'Putin', 'birth_date': '1952-10-07', 'death_date': None, 'place_of_birth': 'Saint Petersburg', 'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9F%D1%83%D1%82%D0%B8%D0%BD,_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80%D0%BE%D0%B2%D0%B8%D1%87', 'start_mandate': '2000-05-07', 'end_mandate': '2008-05-07'}, {'id': 'Q23530', 'first_name': 'Dmitry', 'last_name': 'Medvedev', 'birth_date': '1965-09-14', 'death_date': None, 'place_of_birth': 'Saint Petersburg', 'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9C%D0%B5%D0%B4%D0%B2%D0%B5%D0%B4%D0%B5%D0%B2,_%D0%94%D0%BC%D0%B8%D1%82%D1%80%D0%B8%D0%B9_%D0%90%D0%BD%D0%B0%D1%82%D0%BE%D0%BB%D1%8C%D0%B5%D0%B2%D0%B8%D1%87', 'start_mandate': '2008-05-07', 'end_mandate': '2012-05-07'}, {'id': 'Q34453', 'first_name': 'Boris', 'last_name': 'Yeltsin', 'birth_date': '1931-02-01', 'death_date': '2007-04-23', 'place_of_birth': 'Butka', 'wikipe

## Extracting data from Wikipedia

Query one of the leaders' Wikipedia urls and display its `text` (not JSON).

In [10]:
# 3 lines
def get_wikipedia_url():
    wikipedia_url = leaders_per_country["us"][1]['wikipedia_url']
    print(requests.get(wikipedia_url).content)
    return wikipedia_url
wikipedia_url = get_wikipedia_url()

b'<!DOCTYPE html>\n<html class="client-nojs" lang="en" dir="ltr">\n<head>\n<meta charset="UTF-8"/>\n<title>Barack Obama - Wikipedia</title>\n<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"79ef0f79-9d2a-4405-9571-11f51994f5b0","wgCSPNonce":false,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Barack_Obama","wgTitle":"Barack Obama","wgCurRevisionId":1112320367,"wgRevisionId":1112320367,"wgArticleId":534366,"wgIsArticle":true,"wgIsRedirect":false,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Webarchive template wayback links","CS1 Indonesian-language sources (id)","Pages containing links to subscription-only content","Articles with short d

In [11]:
print(wikipedia_url)

https://en.wikipedia.org/wiki/Barack_Obama


Ouch! You get the raw HTML code of the webpage. If you try to deal with it without tools, you will be there all night. Instead, use the [beautiful soup 4](https://www.crummy.com/software/BeautifulSoup/bs4/doc/) *external* library. You will find more info about it [here](../../2.python/2.python_advanced/05.Scraping/1.beautifulsoup_basic.ipynb) and [here](../../2.python/2.python_advanced/05.Scraping/2.beautifulsoup_advanced.ipynb)

Using the Quickstart section, start by importing the library and loading the output of your `get_text()` function.

Use the `prettify()` function to take a look. You will start the actual parsing in the next step.

In [12]:
from bs4 import BeautifulSoup
leader_content = requests.get(wikipedia_url).content
soup = BeautifulSoup(leader_content, "html")
print(soup)


<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
<head>
<meta charset="utf-8"/>
<title>Barack Obama - Wikipedia</title>
<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"79ef0f79-9d2a-4405-9571-11f51994f5b0","wgCSPNonce":false,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Barack_Obama","wgTitle":"Barack Obama","wgCurRevisionId":1112320367,"wgRevisionId":1112320367,"wgArticleId":534366,"wgIsArticle":true,"wgIsRedirect":false,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Webarchive template wayback links","CS1 Indonesian-language sources (id)","Pages containing links to subscription-only content","Articles with short descript

That looks better but you need to extract the right part of the webpage: the text of the first paragraph.

It is a bit tricky because Wikipedia pages slightly differ in structure from one language to the next. We cannot simply get the text for the first HTML paragraph.

You will start by getting all the HTML paragraphs from the HTML source and saving them in the `paragraphs` variable.

Use the documentation or google the appropriate keywords.

In [13]:
# 2 lines
paragraphs = soup.find_all("p")
print(paragraphs)
    



[<p class="mw-empty-elt">
</p>, <p><b>Barack Hussein Obama II</b> (<span class="rt-commentedText nowrap"><span class="IPA nopopups noexcerpt" lang="en-fonipa"><a href="/wiki/Help:IPA/English" title="Help:IPA/English">/<span style="border-bottom:1px dotted"><span title="'b' in 'buy'">b</span><span title="/ə/: 'a' in 'about'">ə</span><span title="/ˈ/: primary stress follows">ˈ</span><span title="'r' in 'rye'">r</span><span title="/ɑː/: 'a' in 'father'">ɑː</span><span title="'k' in 'kind'">k</span></span><span class="wrap"> </span><span style="border-bottom:1px dotted"><span title="'h' in 'hi'">h</span><span title="/uː/: 'oo' in 'goose'">uː</span><span title="/ˈ/: primary stress follows">ˈ</span><span title="'s' in 'sigh'">s</span><span title="/eɪ/: 'a' in 'face'">eɪ</span><span title="'n' in 'nigh'">n</span></span><span class="wrap"> </span><span style="border-bottom:1px dotted"><span title="/oʊ/: 'o' in 'code'">oʊ</span><span title="/ˈ/: primary stress follows">ˈ</span><span title="'b' 

If you try different urls, you might find that the paragraph you want may be at a different index each time.

That is where you need to be clever and ask yourself what would be a reliable way to identify the right index ie. which string matches only the first paragraph whatever the language...

Spend a good 30 minutes on the problem and brainstorm with your fellow learners. If you come out empty handed, ask your coach.

1. Loop over the HTML paragraphs
2. When you have identified the correct one
  * store the [text](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#output) inside the `first_paragraph` variable
  * exit the loop

At this stage, you can create a function to maintain consistency in your code. We will give you its *skeleton*, you will copy the code you wrote and make it work inside a function.

Don't forget to test your function.

In [14]:
# 6 lines
for paragraph in paragraphs:
    if str(paragraph)[3:6] =="<b>":
        first_paragraph = paragraph
        break
        
print(first_paragraph)

        


<p><b>Barack Hussein Obama II</b> (<span class="rt-commentedText nowrap"><span class="IPA nopopups noexcerpt" lang="en-fonipa"><a href="/wiki/Help:IPA/English" title="Help:IPA/English">/<span style="border-bottom:1px dotted"><span title="'b' in 'buy'">b</span><span title="/ə/: 'a' in 'about'">ə</span><span title="/ˈ/: primary stress follows">ˈ</span><span title="'r' in 'rye'">r</span><span title="/ɑː/: 'a' in 'father'">ɑː</span><span title="'k' in 'kind'">k</span></span><span class="wrap"> </span><span style="border-bottom:1px dotted"><span title="'h' in 'hi'">h</span><span title="/uː/: 'oo' in 'goose'">uː</span><span title="/ˈ/: primary stress follows">ˈ</span><span title="'s' in 'sigh'">s</span><span title="/eɪ/: 'a' in 'face'">eɪ</span><span title="'n' in 'nigh'">n</span></span><span class="wrap"> </span><span style="border-bottom:1px dotted"><span title="/oʊ/: 'o' in 'code'">oʊ</span><span title="/ˈ/: primary stress follows">ˈ</span><span title="'b' in 'buy'">b</span><span title="/

In [15]:
# 10 lines
def get_first_paragraph1(wikipedia_url):
    print(wikipedia_url) # keep this for the rest of the notebook
    #   [insert your code]
    for paragraph in paragraphs:
        if str(paragraph)[3:6] =="<b>":
            first_paragraph = paragraph.text
            break     
        
    return first_paragraph
get_first_paragraph1(wikipedia_url)

https://en.wikipedia.org/wiki/Barack_Obama


'Barack Hussein Obama II (/bəˈrɑːk huːˈseɪn oʊˈbɑːmə/ (listen) bə-RAHK hoo-SAYN oh-BAH-mə;[1] born August 4, 1961) is an American politician who served as the 44th president of the United States from 2009 to 2017. A member of the Democratic Party, he was the first African-American  president of the United States.[2] Obama previously served as a U.S. senator from Illinois from 2005 to 2008 and as an Illinois state senator from 1997 to 2004. \n'

### Regular expressions to the rescue

Now that you have extracted the content of the first paragraph, the only thing that remains to finish your Wikipedia scraper is to sanitize the output.

Indeed some Wikipedia references, HTML code, phonetic pronunciation etc. may linger. You might find *regular expressions* handy to get rid of them and obtain pristine text. You will find some useful documentation about regular expressions [here](../../2.python/2.python_advanced/03.Regex/regex.ipynb)

Once you have one of your regex working online, try it in the cell below. 

Hints: 
* Check the `sub()` method documentation.
* Make sure to test urls in different languages. Some may look good but other do not.

In [16]:
# 4 lines
import re
compiled = re.compile(r'<[^>]+>')
compiled.sub('',str(first_paragraph))


'Barack Hussein Obama II (/bəˈrɑːk huːˈseɪn oʊˈbɑːmə/ (listen) bə-RAHK hoo-SAYN oh-BAH-mə;[1] born August 4, 1961) is an American politician who served as the 44th president of the United States from 2009 to 2017. A member of the Democratic Party, he was the first African-American  president of the United States.[2] Obama previously served as a U.S. senator from Illinois from 2005 to 2008 and as an Illinois state senator from 1997 to 2004. \n'

Overwrite the `get_first_paragraph()` function by applying your regex to the first paragraph before returning it.

In [17]:
# 10 lines

def get_first_paragraph(wikipedia_url):
    print(wikipedia_url) # keep this for the rest of the notebook
    #   [insert your code]
    for paragraph in paragraphs:
        if str(paragraph)[3:6] =="<b>":
            string = str(paragraph)
            break
    # use regex to clean the paragraph
    first_paragraph = compiled.sub('',string)       
    return first_paragraph

get_first_paragraph(wikipedia_url)


https://en.wikipedia.org/wiki/Barack_Obama


'Barack Hussein Obama II (/bəˈrɑːk huːˈseɪn oʊˈbɑːmə/ (listen) bə-RAHK hoo-SAYN oh-BAH-mə;[1] born August 4, 1961) is an American politician who served as the 44th president of the United States from 2009 to 2017. A member of the Democratic Party, he was the first African-American  president of the United States.[2] Obama previously served as a U.S. senator from Illinois from 2005 to 2008 and as an Illinois state senator from 1997 to 2004. \n'

Come up with other regexes to capture other patterns and sanitize the outputs completely. Modify your `get_first_paragraph()` function accordingly.

In [18]:
# < 20 lines

def get_first_paragraph3(wikipedia_url):
    print(wikipedia_url) # keep this for the rest of the notebook
    #   [insert your code]
    leader_content = requests.get(wikipedia_url).content
    soup = BeautifulSoup(leader_content, "html")
    paragraphs = soup.find_all("p")
    for paragraph in paragraphs:
        if str(paragraph)[3:6] =="<b>":
            string = str(paragraph)
            break
    # use regex to clean the paragraph
    first_paragraph = compiled.sub('',string)       
    return first_paragraph




### Caching
Good job! This function will be called many times. First because there are many leaders to loop through. Second because you are developing your code and are likely to re-run your loop multiple times. Third because the API might change and contain new leaders and you might want to update your data periodically.

For all these reasons, it can be benificial to *cache* the result of the `get_first_paragraph()` function so that if it called with the same parameter, you expect the same output and thus do not need to query Wikipedia another time.

You will use the [lru_cache](https://docs.python.org/3/library/functools.html#functools.lru_cache) decorator from the `functools` module. It is a tiny code change that will speed things up big time. You can use a `maxsize` of None. If you have questions about decorators, you will find more information [here](../../2.python/2.python_advanced/07.Decorator/decorators.ipynb)

In [19]:
from functools import lru_cache
@lru_cache(maxsize=None)
def get_first_paragraph(wikipedia_url):
    print(wikipedia_url) # keep this for the rest of the notebook
    #   [insert your code]
    leader_content = requests.get(wikipedia_url).content
    soup = BeautifulSoup(leader_content, "html")
    paragraphs = soup.find_all("p")
    for paragraph in paragraphs:
        if str(paragraph)[3:6] =="<b>":
            string = str(paragraph)
            break
    # use regex to clean the paragraph
    first_paragraph = compiled.sub('',string)       
    return first_paragraph


Let's check the speedup!

In [20]:
%%timeit
get_first_paragraph(wikipedia_url)

https://en.wikipedia.org/wiki/Barack_Obama
The slowest run took 12.67 times longer than the fastest. This could mean that an intermediate result is being cached.
929 ns ± 1.18 µs per loop (mean ± std. dev. of 7 runs, 1 loop each)


## Putting it all together

Let's go back to your `get_leaders()` function and update it with an *inner* loop over each leader. You will query the url provided and extract the first paragraph using the `get_first_paragraph()` function you just finished. You will then update that `leader`'s dictionary and move on to the next one.

Notice, the rest of the code should not change since you modify the leader's data one by one.

In [21]:
def get_leaders():
    root_url = "https://country-leaders.herokuapp.com"
    country_url = "/countries"
    cookie_url = "/cookie"
    leaders_url = "/leaders"
    req = requests.get(f"{root_url}{cookie_url}")
    cookies =req.json()
    countries = requests.get(f"{root_url}{country_url}",cookies = req.cookies)
    dic = {}
    
    for country in countries.json():
        leaders  = requests.get(f"{root_url}{leaders_url}", cookies = req.cookies, params ={"country":country}) 
        dic[country] = leaders.json()
    for country in dic:
        for leader in dic[country]:
            wikipedia_url= leader['wikipedia_url']
            if len(wikipedia_url) == 0:continue
            leader['paragraph'] = get_first_paragraph(wikipedia_url)
        
    return dic
        
    
    


In [22]:
# Check the output of your function (2 lines)
get_leaders()

https://ru.wikipedia.org/wiki/%D0%9F%D1%83%D1%82%D0%B8%D0%BD,_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80%D0%BE%D0%B2%D0%B8%D1%87
https://ru.wikipedia.org/wiki/%D0%9C%D0%B5%D0%B4%D0%B2%D0%B5%D0%B4%D0%B5%D0%B2,_%D0%94%D0%BC%D0%B8%D1%82%D1%80%D0%B8%D0%B9_%D0%90%D0%BD%D0%B0%D1%82%D0%BE%D0%BB%D1%8C%D0%B5%D0%B2%D0%B8%D1%87
https://ru.wikipedia.org/wiki/%D0%95%D0%BB%D1%8C%D1%86%D0%B8%D0%BD,_%D0%91%D0%BE%D1%80%D0%B8%D1%81_%D0%9D%D0%B8%D0%BA%D0%BE%D0%BB%D0%B0%D0%B5%D0%B2%D0%B8%D1%87
https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Hollande
https://fr.wikipedia.org/wiki/Nicolas_Sarkozy
https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Mitterrand
https://fr.wikipedia.org/wiki/Charles_de_Gaulle
https://fr.wikipedia.org/wiki/Jacques_Chirac
https://fr.wikipedia.org/wiki/Val%C3%A9ry_Giscard_d%27Estaing
https://fr.wikipedia.org/wiki/Georges_Pompidou
https://fr.wikipedia.org/wiki/Adolphe_Thiers
https://fr.wikipedia.org/wiki/Napol%C3%A9on_III
https://fr.wikipe

{'ru': [{'id': 'Q7747',
   'first_name': 'Vladimir',
   'last_name': 'Putin',
   'birth_date': '1952-10-07',
   'death_date': None,
   'place_of_birth': 'Saint Petersburg',
   'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9F%D1%83%D1%82%D0%B8%D0%BD,_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80%D0%BE%D0%B2%D0%B8%D1%87',
   'start_mandate': '2000-05-07',
   'end_mandate': '2008-05-07',
   'paragraph': 'Влади́мир Влади́мирович Пу́тин (род. 7 октября 1952, Ленинград, СССР)\xa0— российский государственный, политический и военный деятель. Действующий президент Российской Федерации, председатель Государственного Совета Российской Федерации и верховный главнокомандующий Вооружёнными силами Российской Федерации с 7\xa0мая 2012 года. Ранее занимал должность президента с 7\xa0мая 2000\xa0года по 7\xa0мая 2008 года, также в 1999—2000 и 2008—2012 годах занимал должность председателя правительства Российской Федерации. Кандидат экономических

Does the function crash in the middle of the loop? Chances are the cookies have expired while looping over the leaders.

Modify your function to check if the `status_code` is a cookie error. In which case, get new ones and query the api again.

If not, you may have a fast connection or a bit of luck. Do it anyway.

In [23]:
# 22 lines
def get_leaders():
    root_url = "https://country-leaders.herokuapp.com"
    country_url = "/countries"
    cookie_url = "/cookie"
    leaders_url = "/leaders"
    
    
    # create function to create cookies
    def create_cookies():
        req = requests.get(f"{root_url}{cookie_url}")
        cookies = req.json()
        return req
    
    # create cookies by call calling the create_cookies function
    cookies = create_cookies()
    
    # get the countries
    countries = requests.get(f"{root_url}{country_url}",cookies = cookies.cookies)    
    # initialize a dictionary for leaders data
    dic = {}
    #for every country get its leader info and put in the dic
    for country in countries.json():
        leaders  = requests.get(f"{root_url}{leaders_url}", cookies = cookies.cookies, params ={"country":country}) 
        # check if cookies is valid and create if it is missing
        if leaders.status_code!= 200:
            cookies = create_cookies()
            leaders  = requests.get(f"{root_url}{leaders_url}", cookies = cookies.cookies, params ={"country":country})
            
        dic[country] = leaders.json()
    # go to a country in the dictionary    
    for country in dic:
        # pick a leader, find their wikipedia_url, and get the first pargraph for each leader of that country 
        for leader in dic[country]:
            wikipedia_url= leader['wikipedia_url']
            if len(wikipedia_url) == 0:continue
            leader['paragraph'] = get_first_paragraph(wikipedia_url)
        
    return dic
        
    
    



Check the output of your function again.

In [24]:
%%time
# Check the output of your function (1 line)
get_leaders()


Wall time: 1.42 s


{'ru': [{'id': 'Q7747',
   'first_name': 'Vladimir',
   'last_name': 'Putin',
   'birth_date': '1952-10-07',
   'death_date': None,
   'place_of_birth': 'Saint Petersburg',
   'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9F%D1%83%D1%82%D0%B8%D0%BD,_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80%D0%BE%D0%B2%D0%B8%D1%87',
   'start_mandate': '2000-05-07',
   'end_mandate': '2008-05-07',
   'paragraph': 'Влади́мир Влади́мирович Пу́тин (род. 7 октября 1952, Ленинград, СССР)\xa0— российский государственный, политический и военный деятель. Действующий президент Российской Федерации, председатель Государственного Совета Российской Федерации и верховный главнокомандующий Вооружёнными силами Российской Федерации с 7\xa0мая 2012 года. Ранее занимал должность президента с 7\xa0мая 2000\xa0года по 7\xa0мая 2008 года, также в 1999—2000 и 2008—2012 годах занимал должность председателя правительства Российской Федерации. Кандидат экономических

Well done! It took a while however... Let's speed things up. The main *bottleneck* is the loop. We call on the Wikipedia website many times.

You will use the same *session* to call all the wikipedia pages. Check the *Advanced Usage* section of the Requests module's documentation.

Start by modifying the `get_first_paragraph()` function to accept a session parameter and adjust the `get()` method call.

In [25]:

# not finished
# use a session to call all the wikipedia pages
#%%timeit
from functools import lru_cache
@lru_cache(maxsize=None)
def get_first_paragraph(wikipedia_url,session):
    print(wikipedia_url) # keep this for the rest of the notebook
    #   [insert your code]
    # adjust the get parameter
    leader_content = session.get(wikipedia_url).content
    soup = BeautifulSoup(leader_content, "html")
    paragraphs = soup.find_all("p")
    for paragraph in paragraphs:
        if str(paragraph)[3:6] =="<b>":
            string = str(paragraph)
            break
    # use regex to clean the paragraph
    first_paragraph = compiled.sub('',string)       
    return first_paragraph

Modify your `get_leaders()` function to make use of a single session for all the Wikipedia calls.
1. create a `Session` object outside of the loop over countries.
2. pass it to the `get_first_paragraph()` function as an argument.

In [26]:
# 22 lines
# not finished
def get_leaders():
    root_url = "https://country-leaders.herokuapp.com"
    country_url = "/countries"
    cookie_url = "/cookie"
    leaders_url = "/leaders"
    
    
    # create function to create cookies
    def create_cookies():
        req = requests.get(f"{root_url}{cookie_url}")
        cookies = req.json()
        return req
    
    # create cookies by call calling the create_cookies function
    cookies = create_cookies()
    
    # get the countries
    countries = requests.get(f"{root_url}{country_url}",cookies = cookies.cookies)    
    # initialize a dictionary for leaders data
    dic = {}
    #for every country get its leader info and put in the dic
    for country in countries.json():
        leaders  = requests.get(f"{root_url}{leaders_url}", cookies = cookies.cookies, params ={"country":country}) 
        # check if cookies is valid and create if it is missing
        if leaders.status_code!= 200:
            cookies = create_cookies()
            leaders  = requests.get(f"{root_url}{leaders_url}", cookies = cookies.cookies, params ={"country":country})
            
        dic[country] = leaders.json()
        
    #create a Session object outside of the loop over countries.
    session= requests.Session()
    
    # go to a country in the dictionary  
    for country in dic:
        # pick a leader, find their wikipedia_url, and get the first pargraph for each leader of that country 
        for leader in dic[country]:
            wikipedia_url= leader['wikipedia_url']
            if len(wikipedia_url) == 0:continue
            leader['paragraph'] = get_first_paragraph(wikipedia_url,session)
        
    return dic
        

Test your new functions.



In [27]:
%%time
leaders_per_country = get_leaders()


https://ru.wikipedia.org/wiki/%D0%9F%D1%83%D1%82%D0%B8%D0%BD,_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80%D0%BE%D0%B2%D0%B8%D1%87
https://ru.wikipedia.org/wiki/%D0%9C%D0%B5%D0%B4%D0%B2%D0%B5%D0%B4%D0%B5%D0%B2,_%D0%94%D0%BC%D0%B8%D1%82%D1%80%D0%B8%D0%B9_%D0%90%D0%BD%D0%B0%D1%82%D0%BE%D0%BB%D1%8C%D0%B5%D0%B2%D0%B8%D1%87
https://ru.wikipedia.org/wiki/%D0%95%D0%BB%D1%8C%D1%86%D0%B8%D0%BD,_%D0%91%D0%BE%D1%80%D0%B8%D1%81_%D0%9D%D0%B8%D0%BA%D0%BE%D0%BB%D0%B0%D0%B5%D0%B2%D0%B8%D1%87
https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Hollande
https://fr.wikipedia.org/wiki/Nicolas_Sarkozy
https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Mitterrand
https://fr.wikipedia.org/wiki/Charles_de_Gaulle
https://fr.wikipedia.org/wiki/Jacques_Chirac
https://fr.wikipedia.org/wiki/Val%C3%A9ry_Giscard_d%27Estaing
https://fr.wikipedia.org/wiki/Georges_Pompidou
https://fr.wikipedia.org/wiki/Adolphe_Thiers
https://fr.wikipedia.org/wiki/Napol%C3%A9on_III
https://fr.wikipe

Using a Session makes the first call to `get_leaders()` faster however, for technical reasons, the `@lru_cache` decorator no longer works. 

Problem: The `session` parameter is not *hashable* and since the cache is a dictionary using all the parameters as key, this poses a problem.

Solution: Create our own cache that only cares about the url.

The code for this is provided. You should only read it.

In [28]:
cache = {}
def hashable_cache(f):
    def inner(url, session):
        if url not in cache:
            cache[url] = f(url, session)
        return cache[url]
    return inner

Overwrite the `get_first_paragraph()` function to use the new decorator like this: `@hashable_cache`.


In [29]:
# <20 lines
from functools import *
@hashable_cache
def get_first_paragraph(wikipedia_url,session):
    print(wikipedia_url) # keep this for the rest of the notebook
    #   [insert your code]
    # adjust the get parameter
    leader_content = session.get(wikipedia_url).content
    soup = BeautifulSoup(leader_content, "html")
    paragraphs = soup.find_all("p")
    for paragraph in paragraphs:
        if str(paragraph)[3:6] =="<b>":
            string = str(paragraph)
            break
    # use regex to clean the paragraph
    first_paragraph = compiled.sub('',string)       
    return first_paragraph

Check that the cache is working again.

In [36]:
%%time
#just run it
leaders_per_country = get_leaders()
print(leaders_per_country)


{'ru': [{'id': 'Q7747', 'first_name': 'Vladimir', 'last_name': 'Putin', 'birth_date': '1952-10-07', 'death_date': None, 'place_of_birth': 'Saint Petersburg', 'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9F%D1%83%D1%82%D0%B8%D0%BD,_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80%D0%BE%D0%B2%D0%B8%D1%87', 'start_mandate': '2000-05-07', 'end_mandate': '2008-05-07', 'paragraph': 'Влади́мир Влади́мирович Пу́тин (род. 7 октября 1952, Ленинград, СССР)\xa0— российский государственный, политический и военный деятель. Действующий президент Российской Федерации, председатель Государственного Совета Российской Федерации и верховный главнокомандующий Вооружёнными силами Российской Федерации с 7\xa0мая 2012 года. Ранее занимал должность президента с 7\xa0мая 2000\xa0года по 7\xa0мая 2008 года, также в 1999—2000 и 2008—2012 годах занимал должность председателя правительства Российской Федерации. Кандидат экономических наук (1997).\n'}, {'id': '

## Saving your hard work

The final step is to save the ``leaders_per_country`` dictionary in the `leaders.json` file using the [json](https://docs.python.org/3/library/json.html) module. Make a tour in our [file handling section](../../2.python/2.python_advanced/04.File-handling/file_handling.ipynb) to know more about how to read and write files using Python.

In [31]:
# 3 lines
import json
with open('leaders.json', 'w') as fp:
    json.dump(leaders_per_country, fp)


Make sure the file can be read back. Write the code to read the file.

In [32]:
#3 lines
with open('leaders.json', 'r') as fp:
    leader_data = json.load(fp)
print(leader_data)
print(type(leader_data))

{'ru': [{'id': 'Q7747', 'first_name': 'Vladimir', 'last_name': 'Putin', 'birth_date': '1952-10-07', 'death_date': None, 'place_of_birth': 'Saint Petersburg', 'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9F%D1%83%D1%82%D0%B8%D0%BD,_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80%D0%BE%D0%B2%D0%B8%D1%87', 'start_mandate': '2000-05-07', 'end_mandate': '2008-05-07', 'paragraph': 'Влади́мир Влади́мирович Пу́тин (род. 7 октября 1952, Ленинград, СССР)\xa0— российский государственный, политический и военный деятель. Действующий президент Российской Федерации, председатель Государственного Совета Российской Федерации и верховный главнокомандующий Вооружёнными силами Российской Федерации с 7\xa0мая 2012 года. Ранее занимал должность президента с 7\xa0мая 2000\xa0года по 7\xa0мая 2008 года, также в 1999—2000 и 2008—2012 годах занимал должность председателя правительства Российской Федерации. Кандидат экономических наук (1997).\n'}, {'id': '

Make a function `save()` to call this code easily.

In [33]:
# 3 lines
def save():
    with open('leaders.json', 'w') as fp:
        json.dump(leaders_per_country, fp)
        
    with open('leaders.json', 'r') as fp:
        leader_data = json.load(fp)
    print(leader_data)
    
    
    


In [34]:
# Call the function (1 line)
save()

{'ru': [{'id': 'Q7747', 'first_name': 'Vladimir', 'last_name': 'Putin', 'birth_date': '1952-10-07', 'death_date': None, 'place_of_birth': 'Saint Petersburg', 'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9F%D1%83%D1%82%D0%B8%D0%BD,_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80%D0%BE%D0%B2%D0%B8%D1%87', 'start_mandate': '2000-05-07', 'end_mandate': '2008-05-07', 'paragraph': 'Влади́мир Влади́мирович Пу́тин (род. 7 октября 1952, Ленинград, СССР)\xa0— российский государственный, политический и военный деятель. Действующий президент Российской Федерации, председатель Государственного Совета Российской Федерации и верховный главнокомандующий Вооружёнными силами Российской Федерации с 7\xa0мая 2012 года. Ранее занимал должность президента с 7\xa0мая 2000\xa0года по 7\xa0мая 2008 года, также в 1999—2000 и 2008—2012 годах занимал должность председателя правительства Российской Федерации. Кандидат экономических наук (1997).\n'}, {'id': '

## Tidy things up in a stand-alone python script

Congratulations! You now have a working scraper! However, your code is scattered throughout this notebook along side the tutorials. Hardly production ready...

Copy and paste what you need in a separate `leaders_scraper.py` file.
Make sure it works by calling `python3 leaders_scraper.py`

## To go further

If you want to practice scraping, you can read this section and tackle the exercise.

You have noticed the API returns very partial results for country leaders. Many are missing. Overwrite the `get_leaders()` function to get its list from Wikipedia and extract their *personal details* from the frame on the side.

Good luck!